## Linking a dataset of real historical persons

In this example, we deduplicate a more realistic dataset. The data is based on historical persons scraped from wikidata. Duplicate records are introduced with a variety of errors introduced.


In [ ]:
# Uncomment and run this cell if you're running in Google Colab.
# !pip install splink pandas

In [ ]:
# !pip install pyarrow fastparquet

In [1]:
from splink import splink_datasets

df = splink_datasets.historical_50k

In [3]:
df.head(20)

unique_id   cluster                                         full_name  \
0    Q2296770-1  Q2296770  thomas clifford, 1st baron clifford of chudleigh   
1    Q2296770-2  Q2296770                               thomas of chudleigh   
2    Q2296770-3  Q2296770               tom 1st baron clifford of chudleigh   
3    Q2296770-4  Q2296770                              thomas 1st chudleigh   
4    Q2296770-5  Q2296770              thomas clifford, 1st baron chudleigh   
5    Q2296770-6  Q2296770                      thomas clifford of chudleigh   
6    Q2296770-7  Q2296770                               tom baron chudleigh   
7    Q2296770-8  Q2296770                        tom clifford, of chudleigh   
8    Q2296770-9  Q2296770                        thomas clifford, chudleigh   
9   Q2296770-10  Q2296770                  thomas clifford, baron chudleigh   
10  Q2296770-11  Q2296770               thomas clifford, clifford chydleigh   
11  Q2296770-12  Q2296770                         rhomas clifford chudleigh   
12  Q2296770-13  Q2296770                                 tom 1st chudleigh   
13  Q2296770-14  Q2296770               thomas 1st baron clifford chudleigh   
14  Q2296770-15  Q2296770                        clifford, 1st of chudleigh   
15  Q2296770-16  Q2296770                         thomzs 1st baron clifford   
16   Q1443188-1  Q1443188                            frank edward brightman   
17   Q1443188-2  Q1443188                            frank edward brightman   
18   Q1443188-3  Q1443188                                   frank brightman   
19   Q1443188-4  Q1443188                              francis ed brightman   

      first_and_surname first_name    surname         dob       birth_place  \
0      thomas chudleigh     thomas  chudleigh  1630-08-01             devon   
1      thomas chudleigh     thomas  chudleigh  1630-08-01             devon   
2         tom chudleigh        tom  chudleigh  1630-08-01             devon   
3      thomas chudleigh     thomas  chudleigh  1630-08-01             devon   
4      thomas chudleigh     thomas  chudleigh  1630-08-01             devon   
5      thomas chudleigh     thomas  chudleigh  1630-08-01        west devon   
6         tom chudleigh        tom  chudleigh  1630-08-01        west devon   
7         tom chudleigh        tom  chudleigh        None             devon   
8      thomas chudleigh     thomas  chudleigh  1630-05-01              None   
9      thomas chudleigh     thomas  chudleigh        None             devon   
10     thomas chydleigh     thomas  chydleigh  1630-08-11             devon   
11     rhomas chudleigh     rhomas  chudleigh  1630-08-01             devon   
12        tom chudleigh        tom  chudleigh        None     drewsteignton   
13     thomas chudleigh     thomas  chudleigh  1638-08-01              None   
14  clifford, chudleigh  clifford,  chudleigh  1630-08-01        west devon   
15      thomzs clifford     thomzs   clifford  1630-08-01              None   
16      frank brightman      frank  brightman  1856-06-18           bristol   
17      frank brightman      frank  brightman  1856-06-18           bristol   
18      frank brightman      frank  brightman  1856-06-18  bristol, city of   
19    francis brightman    francis  brightman  1856-06-18              None   

   postcode_fake gender  occupation  
0       tq13 8df   male  politician  
1       tq13 8df   male  politician  
2       tq13 8df   male  politician  
3       tq13 8hu   None  politician  
4       tq13 8df   None  politician  
5       tq13 8df   male  politician  
6       tq13 8df   None        None  
7       tq13 8df   male  politician  
8           None   None  politician  
9       tq13 8jr   male  politician  
10      tq13 8jr   male        None  
11      tq13 8dg   male  politician  
12      tq13 8df   male  politician  
13      tq1w 8df   male  politician  
14          None   None        None  
15      tq13 8df   male  politician  
16       bs2 0el   male   liturgist  
17

In [4]:
from splink import DuckDBAPI
from splink.exploratory import profile_columns

db_api = DuckDBAPI()
profile_columns(df, db_api, column_expressions=["first_name", "substr(surname,1,2)"])

alt.VConcatChart(...)

In [5]:
from splink import DuckDBAPI, block_on
from splink.blocking_analysis import (
    cumulative_comparisons_to_be_scored_from_blocking_rules_chart,
)

blocking_rules = [
    block_on("substr(first_name,1,3)", "substr(surname,1,4)"),
    block_on("surname", "dob"),
    block_on("first_name", "dob"),
    block_on("postcode_fake", "first_name"),
    block_on("postcode_fake", "surname"),
    block_on("dob", "birth_place"),
    block_on("substr(postcode_fake,1,3)", "dob"),
    block_on("substr(postcode_fake,1,3)", "first_name"),
    block_on("substr(postcode_fake,1,3)", "surname"),
    block_on("substr(first_name,1,2)", "substr(surname,1,2)", "substr(dob,1,4)"),
]

db_api = DuckDBAPI()

cumulative_comparisons_to_be_scored_from_blocking_rules_chart(
    table_or_tables=df,
    blocking_rules=blocking_rules,
    db_api=db_api,
    link_type="dedupe_only",
)

alt.Chart(...)

In [6]:
import splink.comparison_library as cl

from splink import Linker, SettingsCreator

settings = SettingsCreator(
    link_type="dedupe_only",
    blocking_rules_to_generate_predictions=blocking_rules,
    comparisons=[
        cl.ForenameSurnameComparison(
            "first_name",
            "surname",
            forename_surname_concat_col_name="first_name_surname_concat",
        ),
        cl.DateOfBirthComparison(
            "dob", input_is_string=True
        ),
        cl.PostcodeComparison("postcode_fake"),
        cl.ExactMatch("birth_place").configure(term_frequency_adjustments=True),
        cl.ExactMatch("occupation").configure(term_frequency_adjustments=True),
    ],
    retain_intermediate_calculation_columns=True,
)
# Needed to apply term frequencies to first+surname comparison
df["first_name_surname_concat"] = df["first_name"] + " " + df["surname"]
linker = Linker(df, settings, db_api=db_api)

In [7]:
linker.training.estimate_probability_two_random_records_match(
    [
        block_on("first_name", "surname", "dob"),
        block_on("substr(first_name,1,2)", "surname", "substr(postcode_fake,1,2)"),
        block_on("dob", "postcode_fake"),
    ],
    recall=0.6,
)

Probability two random records match is estimated to be  0.000136.
This means that amongst all possible pairwise record comparisons, one in 7,362.31 are expected to match.  With 1,279,041,753 total possible comparisons, we expect a total of around 173,728.33 matching pairs


In [8]:
linker.training.estimate_u_using_random_sampling(max_pairs=5e6)

----- Estimating u probabilities using random sampling -----

Estimated u probabilities using random sampling

Your model is not yet fully trained. Missing estimates for:
    - first_name_surname (no m values are trained).
    - dob (no m values are trained).
    - postcode_fake (no m values are trained).
    - birth_place (no m values are trained).
    - occupation (no m values are trained).


In [9]:
training_blocking_rule = block_on("first_name", "surname")
training_session_names = (
    linker.training.estimate_parameters_using_expectation_maximisation(
        training_blocking_rule, estimate_without_term_frequencies=True
    )
)


----- Starting EM training session -----

Estimating the m probabilities of the model by blocking on:
(l."first_name" = r."first_name") AND (l."surname" = r."surname")

Parameter estimates will be made for the following comparison(s):
    - dob
    - postcode_fake
    - birth_place
    - occupation

Parameter estimates cannot be made for the following comparison(s) since they are used in the blocking rules: 
    - first_name_surname

Iteration 1: Largest change in params was 0.248 in probability_two_random_records_match
Iteration 2: Largest change in params was -0.0925 in the m_probability of postcode_fake, level `Exact match on full postcode`
Iteration 3: Largest change in params was -0.0232 in the m_probability of birth_place, level `Exact match on birth_place`
Iteration 4: Largest change in params was -0.00911 in the m_probability of birth_place, level `Exact match on birth_place`
Iteration 5: Largest change in params was 0.00408 in the m_probability of birth_place, level `All othe

In [10]:
training_blocking_rule = block_on("dob")
training_session_dob = (
    linker.training.estimate_parameters_using_expectation_maximisation(
        training_blocking_rule, estimate_without_term_frequencies=True
    )
)


----- Starting EM training session -----

Estimating the m probabilities of the model by blocking on:
l."dob" = r."dob"

Parameter estimates will be made for the following comparison(s):
    - first_name_surname
    - postcode_fake
    - birth_place
    - occupation

Parameter estimates cannot be made for the following comparison(s) since they are used in the blocking rules: 
    - dob

Iteration 1: Largest change in params was -0.472 in the m_probability of first_name_surname, level `Exact match on first_name_surname_concat`
Iteration 2: Largest change in params was 0.053 in the m_probability of first_name_surname, level `All other comparisons`
Iteration 3: Largest change in params was 0.0176 in the m_probability of first_name_surname, level `All other comparisons`
Iteration 4: Largest change in params was 0.00531 in the m_probability of first_name_surname, level `All other comparisons`
Iteration 5: Largest change in params was 0.00162 in the m_probability of first_name_surname, leve

The final match weights can be viewed in the match weights chart:


In [11]:
linker.visualisations.match_weights_chart()

alt.VConcatChart(...)

In [12]:
linker.evaluation.unlinkables_chart()

alt.LayerChart(...)

In [13]:
df_predict = linker.inference.predict()
df_e = df_predict.as_pandas_dataframe(limit=5)
df_e

Blocking time: 0.34 seconds
Predict time: 0.72 seconds


match_weight  match_probability   unique_id_l  unique_id_r first_name_l  \
0     14.742112           0.999964   Q4846289-15   Q4846289-2       feorge   
1     13.044141           0.999882  Q49850500-11  Q49850500-6          joe   
2     15.554104           0.999979    Q188929-10   Q188929-20          sir   
3     20.586032           0.999999   Q3752781-10   Q3752781-2    feederick   
4     18.727552           0.999998   Q7795136-12   Q7795136-3          tom   

  first_name_r surname_l surname_r first_name_surname_concat_l  \
0       george    carter    carter               feorge carter   
1       joseph    taylor    taylor                  joe taylor   
2          art     evans     evans                   sir evans   
3    frederick     warde     warde             feederick warde   
4       thomas    dobson    dobson                  tom dobson   

  first_name_surname_concat_r  ...  bf_birth_place  bf_tf_adj_birth_place  \
0               george carter  ...        0.161931               1.000000   
1               joseph taylor  ...        1.000000               1.000000   
2                   art evans  ...        1.000000               1.000000   
3             frederick warde  ...        1.000000               1.000000   
4               thomas dobson  ...      161.787701               2.572057   

   occupation_l  occupation_r  gamma_occupation  tf_occupation_l  \
0     cricketer     cricketer                 1         0.121001   
1        singer        singer                 1         0.004389   
2   numismatist   numismatist                 1         0.001503   
3         actor         actor                 1         0.013010   
4          None          None                -1              NaN   

   tf_occupation_r  bf_occupation  bf_tf_adj_occupation match_key  
0         0.121001      20.652104              0.358547         4  
1         0.004389      20.652104              9.884256         4  
2         0.001503      20.652104             28.872431         4  
3         0.013010      20.652104              3.334810         4  
4              NaN       1.000000              1.000000         4  

[5 rows x 42 columns]

You can also view rows in this dataset as a waterfall chart as follows:


In [14]:
records_to_plot = df_e.to_dict(orient="records")
linker.visualisations.waterfall_chart(records_to_plot, filter_nulls=False)

alt.LayerChart(...)

In [15]:
clusters = linker.clustering.cluster_pairwise_predictions_at_threshold(
    df_predict, threshold_match_probability=0.95
)

Completed iteration 1, num representatives needing updating: 853
Completed iteration 2, num representatives needing updating: 203
Completed iteration 3, num representatives needing updating: 68
Completed iteration 4, num representatives needing updating: 9
Completed iteration 5, num representatives needing updating: 1
Completed iteration 6, num representatives needing updating: 0


In [16]:
from IPython.display import IFrame

linker.visualisations.cluster_studio_dashboard(
    df_predict,
    clusters,
    "../../results/50k_cluster.html",
    sampling_method="by_cluster_size",
    overwrite=True,
)

# IFrame(src="../../results/50k_cluster.html", width="100%", height=1200)

# Open the file in your browser
import webbrowser
webbrowser.open("../../results/50k_cluster.html")

True

gio: file:///home/enginux/stage/splink/results/50k_cluster.html: Failed to find default application for content type ‘text/html’


In [17]:
linker.evaluation.accuracy_analysis_from_labels_column(
    "cluster", output_type="accuracy", match_weight_round_to_nearest=0.02
)

Blocking time: 0.51 seconds
Predict time: 0.78 seconds


alt.LayerChart(...)

In [18]:
records = linker.evaluation.prediction_errors_from_labels_column(
    "cluster",
    threshold_match_probability=0.999,
    include_false_negatives=False,
    include_false_positives=True,
).as_record_dict()
linker.visualisations.waterfall_chart(records)

Blocking time: 0.52 seconds
Predict time: 0.34 seconds


alt.LayerChart(...)

In [19]:
# Some of the false negatives will be because they weren't detected by the blocking rules
records = linker.evaluation.prediction_errors_from_labels_column(
    "cluster",
    threshold_match_probability=0.5,
    include_false_negatives=True,
    include_false_positives=False,
).as_record_dict(limit=50)

linker.visualisations.waterfall_chart(records)

Blocking time: 0.52 seconds
Predict time: 0.27 seconds


alt.LayerChart(...)